А. Панасюк БКЛ 182

In [1]:
import sys  
sys.path.insert(0, 'C:/Users/mjo/prozhitotools/')
from prozhitotools import dump
dw = dump.Wrapper(r'C:\Users\mjo\Downloads\prozhito')

In [2]:
import re
import pandas as pd

In [ ]:
pd.set_option('display.max_rows', 300)
pd.set_option('display.max_colwidth', -1)

#### Тз

Предложите подход к **оценке** и **анализу** полученной разметки. Чего вы **ждёте от неё**, какие машина допустила **ошибки**, как их может показаться можным **исправить**. ***Почему современный NER допускает такие ошибки?*** Что вы вообще думаете об этом и смежном?

##### Выборка

Я беру записи из дневников за Рождество и Новый год. В имперской России я беру даты с 25 декабря по 1 января, в советской и постсоветской России я беру 31 декабря, 1 января и 7 января (иначе слишком много записей).

Смотрела тексты и выстраивала гипотезы я по полным выборкам за это время (70 текстов и 243), в выборку для разметки я брала около 12 текстов для каждого из периодов, чтобы было удобно отсматривать вывод.

Для конечного теста я брала только тексты, написанные в Российской империи, так как оставалось мало времени.

Также в Новом году и Рождестве часто подводят итоги года и пишут о чем-то кульминационном и важном, упоминают важные события (вот в 1992 году на НГ многие писали о поздравлении Задорнова). Ну и в принципе ощущение, что на эти зимние праздники многое происходит и можно вытащить что-то неочевидное (например, для меня отдаленной не до конца очевидны религиозные употребления Оно, Провидение с большой буквы).

#### Годы, которые мне показались интересными для проверки

1) Восстание декабристов 1825 (НГ 1826)

2) 1856 Крымская война

3) 1907 год революции

4) 1946 год конца войны

5) 1980 Афганская война

6) 1992 первый новый год в РСФСР

10) новый год 2010 (что-то из совсем современного)

#### Гипотезы

1) Ожидаю, что тэггеры сломаются о дневниковые сокращения (А. В., гн., кн., m-me и т.д.)

**NB** В Прожито есть разметка типа М(арья) И(оановна), так вот, я решила скобки не раскрывать, а удалить такие пояснения для чистоты эксперимента. Потому что при работе с необработанными документами это будет проблемой.

Очевидно, можно прописать какие-то правила, но как бы все это заработало? Правила или нейросеть? Мой вывод в конце тетради.

С неименными сокращениями же проще, нужно составить словарь. (гн - господин и т.д.)

2) Тэггеры будут ломаться на иностранных вставках (французский для 19 века, немецкий для 20 века, остальные языки при встрече)

Гипотеза: в наше время на ин. языках пишут скорее названия брендов, а тогда были и NE, и вставки в речи (иногда с большой буквы), непонятно, как объяснить, где разница.

3) Неожиданные для современного исследователя реалии времени, которые по какой-то причине похожи на NE (как Провидение и т.д.).

00) но и в современных текстах есть много проблем, особенно в блогах, в которых пишут как угодно и очень большая вариативность

##### Предобработка

##### 1. Империя

In [134]:
empire = [1826, 1856, 1907]
ussr_ru = [1946, 1980, 1992, 2010]

In [165]:
empire_df = pd.DataFrame(columns=['author', 'date', 'text'])

In [90]:
pattern = re.compile('\[.+?\]')
pattern_encl = re.compile('\([А-яA-z]+?\)')
pattern_link = re.compile('<.+?>')

In [166]:
for year in empire:
    n_year = dw.notes[(year-1, 12, 25) : (year, 1, 1)]
    for it in n_year:
        diary_text = pattern.sub('', it.text)
        diary_text = pattern_link.sub('', diary_text)
        diary_text = pattern_encl.sub('', diary_text)
        diary_text = diary_text.replace('*', '')
        empire_df = empire_df.append({'author': it.author, 'date': it.date, 'text': diary_text}, ignore_index=True)

In [167]:
len(empire_df)  # всего в выборке 70 текстов для имперской России

70

In [168]:
empire_df

author            date  \
0   #1052 Александр Иванович Тургенев        (1825, 12, 25)   
1   #1052 Александр Иванович Тургенев        (1825, 12, 27)   
2   #849 Василий Андреевич Жуковский         (1825, 12, 28)   
3   #1052 Александр Иванович Тургенев        (1825, 12, 28)   
4   #1052 Александр Иванович Тургенев        (1825, 12, 29)   
5   #1052 Александр Иванович Тургенев        (1825, 12, 30)   
6   #1052 Александр Иванович Тургенев        (1825, 12, 31)   
7   #1052 Александр Иванович Тургенев        (1826, 1, 1)     
8   #635 Александр Васильевич Дружинин       (1855, 12, 25)   
9   #635 Александр Васильевич Дружинин       (1855, 12, 26)   
10  #817 Константин Александрович Успенский  (1855, 12, 26)   
11  #635 Александр Васильевич Дружинин       (1855, 12, 27)   
12  #635 Александр Васильевич Дружинин       (1855, 12, 28)   
13  #635 Александр Васильевич Дружинин       (1855, 12, 30)   
14  #2086 Николай Александрович Добролюбов   (1855, 12, 30)   
15  #635 Александр Васильевич Дружинин       (1855, 12, 31)   
16  #635 Александр Васильевич Дружинин       (1856, 1, 1)     
17  #330 Татьяна  Александровна Найденова    (1906, 12, 25)   
18  #15 Александра  Викторовна Богданович    (1906, 12, 25)   
19  #543 Алиса Георгиевна Коонен             (1906, 12, 25)   
20  #178 Константин Константинович Романов   (1906, 12, 25)   
21  #151 Михаил Алексеевич Кузмин            (1906, 12, 25)   
22  #953 Яков Соломонович Поляков            (1906, 12, 25)   
23  #1376 Владимир Аркадьевич Теляковский    (1906, 12, 25)   
24  #543 Алиса Георгиевна Коонен             (1906, 12, 26)   
25  #178 Константин Константинович Романов   (1906, 12, 26)   
26  #151 Михаил Алексеевич Кузмин            (1906, 12, 26)   
27  #953 Яков Соломонович Поляков            (1906, 12, 26)   
28  #1376 Владимир Аркадьевич Теляковский    (1906, 12, 26)   
29  #543 Алиса Георгиевна Коонен             (1906, 12, 27)   
30  #230 Александр Алексеевич Киреев         (1906, 12, 27)   
31  #178 Константин Константинович Романов   (1906, 12, 27)   
32  #151 Михаил Алексеевич Кузмин            (1906, 12, 27)   
33  #953 Яков Соломонович Поляков            (1906, 12, 27)   
34  #1376 Владимир Аркадьевич Теляковский    (1906, 12, 27)   
35  #330 Татьяна  Александровна Найденова    (1906, 12, 28)   
36  #543 Алиса Георгиевна Коонен             (1906, 12, 28)   
37  #178 Константин Константинович Романов   (1906, 12, 28)   
38  #151 Михаил Алексеевич Кузмин            (1906, 12, 28)   
39  #953 Яков Соломонович Поляков            (1906, 12, 28)   
40  #1376 Владимир Аркадьевич Теляковский    (1906, 12, 28)   
41  #330 Татьяна  Александровна Найденова    (1906, 12, 29)   
42  #543 Алиса Георгиевна Коонен             (1906, 12, 29)   
43  #178 Константин Константинович Романов   (1906, 12, 29)   
44  #151 Михаил Алексеевич Кузмин            (1906, 12, 29)   
45  #953 Яков Соломонович Поляков            (1906, 12, 29)   
46  #1383 Фёдор Фёдорович Фидлер             (1906, 12, 29)   
47  #1376 Владимир Аркадьевич Теляковский    (1906, 12, 29)   
48  #543 Алиса Георгиевна Коонен             (1906, 12, 30)   
49  #178 Константин Константинович Романов   (1906, 12, 30)   
50  #151 Михаил Алексеевич Кузмин            (1906, 12, 30)   
51  #953 Яков Соломонович Поляков            (1906, 12, 30)   
52  #2296 Алексей Иванович Коноров           (1906, 12, 30)   
53  #1376 Владимир Аркадьевич Теляковский    (1906, 12, 30)   
54  #543 Алиса Георгиевна Коонен             (1906, 12, 31)   
55  #178 Константин Константинович Романов   (1906, 12, 31)   
56  #178 Константин Константинович Романов   (1906, 12, 31)   
57  #151 Михаил Алексеевич Кузмин            (1906, 12, 31)   
58  #953 Яков Соломонович Поляков            (1906, 12, 31)   
59  #1930 Василий Осипович Ключевский        (1906, 12, 31)   
60  #1376 Владимир Аркадьевич Теляковский    (1906, 12, 31)   
61  #330 Татьяна  Александровна Найденова    (1907, 1, 1)     
62  #15 Александра  Викторовна Богданович    (1907, 1, 1)     
63  #

##### 20-21 век

In [135]:
ussr_rudf = pd.DataFrame(columns=['author', 'date', 'text'])

In [136]:
for year in ussr_ru:
    n_year = dw.notes[(year-1, 12, 31) : (year, 1, 1)]
    print(year)
    print(len(n_year))
    for it in n_year:
        diary_text = pattern.sub('', it.text)
        diary_text = pattern_link.sub('', diary_text)
        diary_text = pattern_encl.sub('', diary_text)
        diary_text = diary_text.replace('*', '')
        ussr_rudf = ussr_rudf.append({'author': it.author, 'date': it.date, 'text': diary_text}, ignore_index=True)
    n_year = dw.notes[(year, 1, 7):(year, 1, 7)]
    print(len(n_year))
    for it in n_year:
        diary_text = pattern.sub('', it.text)
        diary_text = pattern_link.sub('', diary_text)
        diary_text = pattern_encl.sub('', diary_text)
        diary_text = diary_text.replace('*', '')
        ussr_rudf = ussr_rudf.append({'author': it.author, 'date': it.date, 'text': diary_text}, ignore_index=True)

1946
39
12
1980
37
9
1992
10
8
2010
10
4


То, что мало текстов после 1950-го, связано с тем, что дневники того времени еще не передали в Прожито

In [143]:
len(ussr_rudf)

129

In [141]:
ussr_rudf

author            date  \
0    #367 Владимир Алексеевич Порцевский       (1945, 12, 31)   
1    #389 Ирина Мартиновна Дажина              (1945, 12, 31)   
2    #117 Сергей Иванович Вавилов              (1945, 12, 31)   
3    #669 Евгений Иванович Селиванов           (1945, 12, 31)   
4    #150 Юлия Александровна Кривулина         (1945, 12, 31)   
5    #600 Александра  Михалева                 (1945, 12, 31)   
6    #1023 Яков Семёнович Друскин              (1945, 12, 31)   
7    #1012 Сергей Александрович Волков         (1945, 12, 31)   
8    #641 Борис Вульфович Зон                  (1945, 12, 31)   
9    #608 Борис Александрович Андреев          (1945, 12, 31)   
10   #2314 Матрёна Михайловна Джулаева         (1945, 12, 31)   
11   #2311 Татьяна Дмитриевна Булах-Гардина    (1945, 12, 31)   
12   #56 Михаил Михайлович Пришвин             (1945, 12, 31)   
13   #11 Самуил Борисович Бернштейн            (1946, 1, 1)     
14   #152 Тамара Владимировна Лазерсон         (1946, 1, 1)     
15   #314 Владимир  Алексеевич Чивилихин       (1946, 1, 1)     
16   #318 Владимир Афанасьевич Швец            (1946, 1, 1)     
17   #117 Сергей Иванович Вавилов              (1946, 1, 1)     
18   #405 Олекса Іванович Воропай              (1946, 1, 1)     
19   #368 Михаил Вячеславович Матов            (1946, 1, 1)     
20   #368 Михаил Вячеславович Матов            (1946, 1, 1)     
21   #825 Иван Петрович Сусляк                 (1946, 1, 1)     
22   #150 Юлия Александровна Кривулина         (1946, 1, 1)     
23   #600 Александра  Михалева                 (1946, 1, 1)     
24   #198 Любовь Васильевна Шапорина           (1946, 1, 1)     
25   #529 Николай Сергеевич Пашин              (1946, 1, 1)     
26   #1023 Яков Семёнович Друскин              (1946, 1, 1)     
27   #1533 Нина Сергеевна Покровская           (1946, 1, 1)     
28   #608 Борис Александрович Андреев          (1946, 1, 1)     
29   #1989 Георгий Григорьевич Головин         (1946, 1, 1)     
30   #168 Софья Казимировна Островская         (1946, 1, 1)     
31   #712 Павел Яковлевич Зальцман             (1946, 1, 1)     
32   #712 Павел Яковлевич Зальцман             (1946, 1, 1)     
33   #2370 Александр Леонидович Слонимский     (1946, 1, 1)     
34   #2311 Татьяна Дмитриевна Булах-Гардина    (1946, 1, 1)     
35   #1653 Зара Григорьевна Минц               (1946, 1, 1)     
36   #2449 Эрмиония Александровна Евлахова     (1946, 1, 1)     
37   #56 Михаил Михайлович Пришвин             (1946, 1, 1)     
38   #2929 Виталий Степанович Буханов          (1946, 1, 1)     
39   #284 Андрей Константинович Буров          (1946, 1, 7)     
40   #335 Сергей Гаврилович Юров               (1946, 1, 7)     
41   #405 Олекса Іванович Воропай              (1946, 1, 7)     
42   #150 Юлия Александровна Кривулина         (1946, 1, 7)     
43   #599 Петр Евграфович Ковалевский          (1946, 1, 7)     
44   #1001 Сергей Сергеевич Трегубов           (1946, 1, 7)     
45   #529 Николай Сергеевич Пашин              (1946, 1, 7)     
46   #1023 Яков Семёнович Друскин              (1946, 1, 7)     
47   #608 Борис Александрович Андреев          (1946, 1, 7)     
48   #2190 Магдалина Михайловна Буркина        (1946, 1, 7)     
49   #867 Евгений Евгеньевич Лансере           (1946, 1, 7)     
50   #56 Михаил Михайлович Пришвин             (1946, 1, 7)     
51   #50 Юрий Маркович Нагибин                 (1979, 12, 31)   
52   #57 Николай Семенович Работнов            (1979, 12, 31)   
53   #318 Владимир Афанасьевич Швец            (1979, 12, 31)   
54   #331 Валерий Иванович Аблазов             (1979, 12, 31)   
55   #453 Александр Дмитриевич Шмеман          (1979, 12, 31)   
56   #460 Петр Степанович Непорожний           (1979, 12, 31)   
57   #254 Натан Яковлевич Эйдельман            (1979, 12, 31)   
58   #188 Андрей Арсеньевич Тарковский         (1979, 12, 31)   
59   #223 Милица Васильевна Нечкина            (1979, 12, 31)   
60   #131 Игорь Александрович Дедков           (1979, 12, 31)   
61   #294

In [175]:
us_ru = ussr_rudf.text  # сокращаю количество текстов для разметки, потому что все ломается, когда слишком много, 
ur_texts = '\n\n\n'.join(us_ru[::9])  # и непонятно, как анализировать

In [178]:
emptexts = empire_df.text
emptext = '\n\n\n'.join(emptexts[::10])

#### NER

Про NE я знала, что есть Наташа, поэтому мне нужен был рисерч

Сравнение теггеров: 
https://habr.com/ru/post/502366/

Stanza

Natasha

DeepPavlov (здравствуйте Алиса и Алекса)

deepmipt/ner

Polyglot

PullEnti

##### И еще

куча всего с БЕРТом (для которого я маленькая собачка и его сразу опускаю)
http://docs.deeppavlov.ai/en/master/features/pretrained_vectors.html

И еще:

nltk
ner-ru https://github.com/zamgi/lingvo--Ner-ru

##### Что я беру

В 2016 стал лучшим RuEval **PullEnti** https://github.com/dialogue-evaluation/factRuEval-2016

Так что брать буду его. И буду его сравнивать с наташей.

Потому что pullenti -- rule-based, наташа -- эмбеддинги. А мы ожидаем, что правила на старых текстах не работают.

In [151]:
from pullenti_wrapper.processor import (
    Processor,
    MONEY,
    URI,
    PHONE,
    DATE,
    KEYWORD,
    DEFINITION,
    DENOMINATION,
    MEASURE,
    BANK,
    GEO,
    ADDRESS,
    ORGANIZATION,
    PERSON,
    MAIL,
    TRANSPORT,
    DECREE,
    INSTRUMENT,
    TITLEPAGE,
    BOOKLINK,
    BUSINESS,
    NAMEDENTITY,
    WEAPON,
)

In [186]:
result = processor(emptext)

In [197]:
matches = []
if result.matches != []:
    for match in result.matches:
        matches.append(match)

In [270]:
matches = result.matches

In [268]:
emppul = pd.DataFrame(columns=['label', 'slots'])  # пустой дф чтобы туда записать найденные мэтчи

In [271]:
len(matches)  # их 78

78

In [272]:
for match in matches:
    label = match.referent.label
    emppul = emppul.append({'label':label, 'slots':match.referent.slots}, ignore_index=True)

In [273]:
emppul  # записываю я очень непорядочно, но так хотя бы видно. Я не знаю, сколько может быть в теории слотов, так что пусть

label  \
0   PERSON         
1   PERSON         
2   PERSON         
3   GEO            
4   GEO            
5   GEO            
6   GEO            
7   PERSON         
8   GEO            
9   GEO            
10  PERSON         
11  PERSON         
12  PERSON         
13  PERSON         
14  DATE           
15  DATE           
16  PERSON         
17  PERSON         
18  DATE           
19  DATE           
20  GEO            
21  GEO            
22  GEO            
23  GEO            
24  GEO            
25  DATE           
26  PERSON         
27  GEO            
28  GEO            
29  PERSON         
30  GEO            
31  MONEY          
32  PERSON         
33  GEO            
34  GEO            
35  GEO            
36  ORGANIZATION   
37  GEO            
38  DATE           
39  PERSON         
40  GEO            
41  GEO            
42  GEO            
43  DATE           
44  GEO            
45  DATE           
46  PERSON         
47  MONEY          
48  DATE           
49  DATE           
50  GEO            
51  PERSON         
52  ORGANIZATION   
53  DATE           
54  PERSON         
55  PERSON         
56  PERSON         
57  DATE           
58  PERSON         
59  PERSON         
60  DATE           
61  DATE           
62  PERSON         
63  ORGANIZATION   
64  DATE           
65  PERSON         
66  PERSON         
67  DATE           
68  PERSON         
69  PERSON         
70  DATE           
71  DATE           
72  GEO            
73  DATE           
74  DATE           
75  GEO            
76  ORGANIZATION   
77  ORGANIZATION   

                                                                                                                                                                                                                                                                                                                                                             slots  
0   [Slot(key='SEX', value='MALE'), Slot(key='LASTNAME', value='САНИН'), Slot(key='FIRSTNAME', value='АЛЕКСАНДР')]                                                                                                                                                                                                                                                  
1   [Slot(key='SEX', value='MALE'), Slot(key='LASTNAME', value='САНИН'), Slot(key='FIRSTNAME', value='АЛЕКСАНДР')]                                                                                                                                                                                                                                                  
2   [Slot(key='SEX', value='MALE'), Slot(key='LASTNAME', value='САНИН'), Slot(key='FIRSTNAME', value='АЛЕКСАНДР')]                                                                                                                                                                                                                                                  
3   [Slot(key='NAME', value='ВЕНА'), Slot(key='TYPE', value='город')]                                                                                                                                                                                                                                                                                               
4   [Slot(key='ALPHA2', value='RU'), Slot(key='NAME', value='РФ'), Slot(key='NAME', value='РОССИЙСКАЯ ФЕДЕРАЦИЯ'), Slot(key='NAME', value='РОССИЯ'), Slot(key='TYPE', value='государство')]                                                                                                                                                                         
5   [Slot(key='ALPHA2', value='RU'), Slot(key='NAME', value='РФ'), Slot(key='NAME', value='РОССИЙСКАЯ ФЕДЕРАЦИЯ'), Slot(key='NAME', value='РОССИЯ'), Slot(key='TYPE', value='государство')]                                                                                                     

##### Вывод pullenti

Видно, что хорошо достает названия городов, стран и понятные фамилии (а вот имя императора Александра почему-то не достал и объединил его с фамилией Санин. Потому что в конце один раз упоминается Александр Санин). Также разобрал "министерство двора", т.к. это вполне себе могущая входить в rules вхождение.

Не разобрался и с сокращениями.

Не достал имя императора Павла.

Не достал иностранные имена, хотя мог бы. "Вечер у мудреца Royer-Collard". ( а вот Наташа подумала, что это организация, но хотя бы подумала). Не разобралси НИ С КАКИМИ иностранным именами. Наташа хотя бы некоторые поняла.

Не достал названия "Гулльский инцидент", название город Гулль.

##### В общем, в старых текстах не до правил

In [267]:
result

Result(
    text='1 час пополудни. Сию минуту возвратился из русской церкви: мы служили панихиду по незабвенном императоре, — и возносили на литургии имя нового! Почти все русские были в церкви. Трудно выразить впечатление, которое произвела на меня молитва о усопшем! Я озирался вокруг себя и видел памятники, живые, царствования Александра, из коих некоторые принадлежат истории, другие останутся в записках двора или по крайней мере в анекдотах его. Посол, коего политическое бытие сотворил Александр всемогуществом своего сана — и стечением необыкновенных обстоятельств; за ним памятник пяти царствований — светлейший Разумовский, еще бодрящийся, но уже не бодрствующий у чужих престолов, обязанный Александру настоящим благосостоянием своим, утратив прежнее с обгорелыми развалинами великолепного дворце своего в Вене. Далее Чичагов, непримиримый враг русского правительства, смелый говорун в собрании министров и Совета, мечтающий иметь право злословить Россию в лице ее правителей и привязавши

### Наташа

In [259]:
from navec import Navec
from slovnet import NER
from ipymarkup import show_span_ascii_markup as show_markup

navec = Navec.load('navec_news_v1_1B_250K_300d_100q.tar')
ner = NER.load('slovnet_ner_news_v1.tar')
ner.navec(navec)

markup = ner(emptext)

show_markup(markup.text, markup.spans)

1 час пополудни. Сию минуту возвратился из русской церкви: мы служили 
панихиду по незабвенном императоре, — и возносили на литургии имя 
нового! Почти все русские были в церкви. Трудно выразить впечатление, 
которое произвела на меня молитва о усопшем! Я озирался вокруг себя и 
видел памятники, живые, царствования Александра, из коих некоторые 
                                     PER───────                    
принадлежат истории, другие останутся в записках двора или по крайней 
мере в анекдотах его. Посол, коего политическое бытие сотворил 
Александр всемогуществом своего сана — и стечением необыкновенных 
PER──────                                                         
обстоятельств; за ним памятник пяти царствований — светлейший 
Разумовский, еще бодрящийся, но уже не бодрствующий у чужих престолов,
PER────────                                                           
 обязанный Александру настоящим благосостоянием своим, утратив прежнее
           PER───────                  

In [262]:
doc_ner = ner(emptext)

In [264]:
len(doc_ner.spans)

136

Наташа молодец, даже с сокращениями разобралась. И Ал, и Кн Тюфякин были пойманы.

Иностранщиу на нерусском впрочем тоже не везде поймала.

Не везде выделила города (Паловск), имена (Георгию). Очевидно, дело в том, что они 1-ые в строке и с большой буквы, и Наташа списала это на начало строки (А потом, когда Павловск не в начале строки, нашла).

Из-за этого же выделила Мама как NE, хотя Мама это родственная мама.

Не выделила Иоанна Грозного в кавычках :( pullenti выделил. Очевидно, потому, что когда-то наташе сказали, что не все, что в кавычках -- имя собственное, а может быть например (цитата), и склонилось к этому варианту.

**Но в целом разбор вышел вполне приличным**

### Вывод

Наташа (точнее, словнет) с эмбеддингами (новостными) справилась лучше, чем более rule-based pullenti на старом тексте. 136 NE vs 78.

Предложите подход к оценке и анализу полученной разметки. Чего вы ждёте от неё, какие машина допустила ошибки, как их может показаться можным исправить. Почему современный NER допускает такие ошибки? Что вы вообще думаете об этом и смежном?

Почему так? Наташа больше настроена на "догадывание", а не на правила. И для более старого материала этот подход выграл.

Возможно, стоит к гибкости эмбеддингов добавить еще правил, которые бы описывали особенности письма того времени, и тогда было бы шикарно. Или было бы еще лучше обучить модель на разметке текстов того времени. И, например, объяснить, что вот такие сочетания нерусскоязычных символов в тексте тоже могли быть именами.

Как подходить к анализу? Разбивать на классы и смотреть, где кому что удалось сделать, а где нет. Оценивать так же и брать от подходов лучшее.